In [1]:
!pip install --upgrade --no-dependencies llm_bhasa
!pip install more-itertools

# Download Gutenberg dataset

In [2]:
!du -sh /kaggle/input/download-gutenberg-book-dataset

480K	/kaggle/input/download-gutenberg-book-dataset


In [3]:
import os
import pandas as pd

bookkeep_filepath_archive = "/kaggle/input/download-gutenberg-book-dataset/guthenberg_bookkeeper.csv"
bookkeep_filepath = "/kaggle/working/guthenberg_bookkeeper.csv"

def read_bookkeep(bookkeep_filepath):
    if os.path.exists(bookkeep_filepath):
        df_bookkeep = pd.read_csv(bookkeep_filepath)
    else:
        df_bookkeep = pd.DataFrame([], columns=['book_id', 'status', 'num_tokens'])
    return df_bookkeep

df_bookkeep = read_bookkeep(bookkeep_filepath_archive)
df_bookkeep

book_id  status  num_tokens
0           0   False           0
1           1    True       31044
2           2   False           0
3           3    True        2059
4           4   False           0
...       ...     ...         ...
4995     4995   False           0
4996     4996   False           0
4997     4997    True       99562
4998     4998   False           0
4999     4999   False           0

[5000 rows x 3 columns]

In [4]:
df_bookkeep['book_id'].max()

4999

In [5]:
gutenberg_book_ids = list(range(500000))

In [6]:
gutenberg_book_ids_visited = df_bookkeep['book_id'].tolist()
gutenberg_book_ids_remaining = list(set(gutenberg_book_ids) - set(gutenberg_book_ids_visited))

print(f"Total book_ids: {len(gutenberg_book_ids)}")
print(f"Total visited book_ids: {len(gutenberg_book_ids_visited)}")
print(f"Total remaining book_ids: {len(gutenberg_book_ids_remaining)}")

Total book_ids: 500000
Total visited book_ids: 5000
Total remaining book_ids: 495000


In [7]:
from more_itertools import chunked
chunk_size = 1000
chunks = list(chunked(gutenberg_book_ids_remaining, chunk_size))
print(f"Total chunks: {len(chunks)}")

Total chunks: 495


In [8]:
%%time

from llm_bhasa.harmony import data
from llm_bhasa.harmony import tokenizer as tokenizer_lib
from tqdm.contrib.concurrent import process_map

tokenizer = tokenizer_lib.get_tokenizer()
resultset = df_bookkeep.to_dict(orient='records')

def _read_from_url(book_id):
    book_url = "https://www.gutenberg.org/files/{}/{}-0.txt".format(book_id, book_id)
    status, text = data.read_from_url(book_url)
    num_tokens = len(tokenizer.encode(text)) if status else 0
    return book_id, status, num_tokens

njobs = 10
for cntr, chunk in enumerate(chunks):
    print(f"vising chunk: {cntr + 1}")
    result = process_map(_read_from_url, 
                         chunk,              
                         max_workers=njobs,
                         chunksize=1,
                         desc=f"Reading gutenberg books")
    
    for book_id, status, num_tokens in result:
        resultset.append({
            'book_id': book_id, 
            'status': status,
            'num_tokens': num_tokens
        })
    pd.DataFrame(resultset).to_csv(bookkeep_filepath, index=False)

vising chunk: 1


Reading gutenberg books:   0%|          | 0/1000 [00:00<?, ?it/s]

vising chunk: 2


Reading gutenberg books:   0%|          | 0/1000 [00:00<?, ?it/s]

vising chunk: 3


...

vising chunk: 494


Reading gutenberg books:   0%|          | 0/1000 [00:00<?, ?it/s]

vising chunk: 495


Reading gutenberg books:   0%|          | 0/1000 [00:00<?, ?it/s]

CPU times: user 10min 42s, sys: 3min 2s, total: 13min 44s
Wall time: 2h 32min 4s
